## Bus Stops in Pittsburgh

In [5]:
import geopandas as gpd
import folium
import math


# data
gdf = gpd.read_file("prt-stops.geojson")

# center, map
center = [gdf.geometry.y.mean(), gdf.geometry.x.mean()]
m = folium.Map(location=center, zoom_start=12)


# bus stop
for _, row in gdf.iterrows():
    folium.CircleMarker(
        location=[row.geometry.y, row.geometry.x],
        radius=1,
        color='red',
        fill=True,
        fill_opacity=0.7
    ).add_to(m)

m.add_child(folium.LatLngPopup())

m.save("pittsburgh_bus_stops.html")
m


## The funtion for counting stops in an area

In [6]:
def count_stops_simple(lat, lon, radius_miles, gdf):
    """
    lat, lon : center coordinates (degrees)
    radius_miles : radius (miles)
    gdf : preloaded GeoDataFrame (assumed EPSG:4326)
    """
    # Approximation: 1 degree of latitude ≈ 69 miles, longitude ≈ 69 * cos(latitude)
    lat_per_mile = 1 / 69.0
    lon_per_mile = 1 / (69.0 * math.cos(math.radians(lat)))

    # Convert radius to degrees
    dlat = radius_miles * lat_per_mile
    dlon = radius_miles * lon_per_mile

    count = 0
    for point in gdf.geometry:
        plat, plon = point.y, point.x
        # Quick bounding-box check
        if abs(plat - lat) <= dlat and abs(plon - lon) <= dlon:
            # Compute simple Euclidean distance in miles
            dist = math.sqrt(((plat - lat)/lat_per_mile)**2 + ((plon - lon)/lon_per_mile)**2)
            if dist <= radius_miles:
                count += 1
    return count

num = count_stops_simple(40.4406, -79.9959, 0.1, gdf)
print(num)

9


## The number of bus stops within 0.3 miles of each neighborhood’s coordinates.

In [7]:
keys_file = "Neighborhood.txt"
values_file = "Latitude.txt"
latitude = {}


with open(keys_file, "r", encoding="utf-8") as kf, open(values_file, "r", encoding="utf-8") as vf:
    for key_line, value_line in zip(kf, vf):
        key = key_line.strip()
        value = value_line.strip()
        if value == '':
            continue
        latitude[key] = float(value)
#print(latitude)

values_file = "longitude.txt"
longitude = {}
with open(keys_file, "r", encoding="utf-8") as kf, open(values_file, "r", encoding="utf-8") as vf:
    for key_line, value_line in zip(kf, vf):
        key = key_line.strip()
        value = value_line.strip()
        if value == '':
            continue
        longitude[key] = float(value)
#print(longitude)

result = {}
for key in latitude:
    if key == '':
        continue
    num = count_stops_simple(float(latitude[key]),float(longitude[key]), 0.3, gdf)
    result[key] = num

#print(result)

sorted_data = dict(sorted(result.items(), key=lambda x: x[1]))
print(sorted_data)


{'Swisshelm Park': 0, 'New Homestead': 0, 'Sheraden': 1, 'Ridgemont': 1, 'Brookline': 3, 'Lincoln Place': 3, 'Crafton Heights': 4, 'South Oakland': 5, 'Banksville': 5, 'Esplen': 5, 'Oakwood': 5, 'Squirrel Hill South': 6, 'Bon Air': 6, 'Hays': 6, 'North Shore': 7, 'Bedford Dwellings': 8, 'Overbrook': 8, 'South Side Slopes': 8, 'St. Clair': 8, 'Carrick': 9, 'Stanton Heights': 9, 'East Carnegie': 9, 'Perry North': 10, 'Duquesne Heights': 10, 'Chateau': 10, 'Chartiers City': 10, 'Windgap': 11, 'West End': 11, 'Fairywood': 12, 'Greenfield': 12, 'Larimer': 12, 'Glen Hazel': 12, 'Central Lawrenceville': 13, 'Marshall-Shadeland': 13, 'Mt. Oliver': 14, 'Summer Hill': 15, 'Arlington Heights': 15, 'Brighton Heights': 17, 'Arlington': 17, 'Point Breeze': 17, 'Bluff': 17, 'Westwood': 17, 'South Shore': 17, 'Squirrel Hill North': 18, 'Manchester': 19, 'Knoxville': 19, 'Elliott': 19, 'Fineview': 20, 'Beechview': 20, 'Middle Hill': 20, 'Garfield': 20, 'Spring Hill-City View': 20, 'Hazelwood': 20, 'Upp

## Visualization of a 0.3-mile radius around each neighborhood.

In [53]:
for key in latitude:
    folium.CircleMarker(
        location=[float(latitude[key]), float(longitude[key])],
        radius=1,
        color='blue',
        fill=True,
        fill_opacity=0.7
    ).add_to(m)
    draw_circle_map(latitude[key],longitude[key],0.3,m)

m.add_child(folium.LatLngPopup())

m.save("pittsburgh_bus_stops.html")
m